# IBM Applied Data Science Capstone – Coursera

# Opening a new pizza place in Boston, USA
** New investor is looking to start a new pizza place in Boston, USA neighborhoods **
- Build a dataframe of neighborhoods of Boston, USA by web scraping the data from Wikipedia page
- Get the geographical coordinates of the neighborhoods
- Obtain the venue data for the neighborhoods from Foursquare API
- Explore and cluster the neighborhoods
- Select the best cluster to open a new pizza place
***
### 1. Import libraries

In [2]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option("display.max_columns", None)
pd.set_option("display.max_rows", None)

import json # library to handle JSON files

from geopy.geocoders import Nominatim # convert an address into latitude and longitude values
import geocoder # to get coordinates

import requests # library to handle requests
from bs4 import BeautifulSoup # library to parse HTML and XML documents

from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

import folium # map rendering library

print("Libraries imported.")

Libraries imported.


### 2. Scrap data from Wikipedia page into a DataFrame

##### send the GET request
data = requests.get("https://en.wikipedia.org/wiki/Greater_Boston").text

In [4]:
# parse data from the html into a beautifulsoup object
soup = BeautifulSoup(data, 'html.parser')

In [5]:
# create a list to store neighborhood data
neighborhoodList = []

In [6]:
# append the data into the list
for row in soup.find_all("div", class_="div-col columns column-width")[0].findAll("li"):
    neighborhoodList.append(row.text)

In [22]:
# create a new DataFrame from the list
kl_df = pd.DataFrame({"Neighborhood": neighborhoodList})
kl_df.sort_values(['Neighborhood'],ascending=True)
kl_df.head(100)

Neighborhood
0           Andover
1         Arlington
2         Attleboro
3            Auburn
4              Avon
5              Ayer
6        Barnstable
7             Barre
8           Bedford
9           Belmont
10        Billerica
11       Blackstone
12           Boston
13         Boylston
14        Braintree
15      Bridgewater
16         Brockton
17       Brookfield
18        Brookline
19       Burlington
20        Cambridge
21           Canton
22          Chelsea
23           Dedham
24          Dighton
25          Duxbury
26  East Brookfield
27           Easton
28        Edgartown
29          Everett
30        Fitchburg
31       Foxborough
32       Framingham
33         Franklin
34          Gardner
35          Grafton
36        Haverhill
37          Hingham
38         Holbrook
39           Holden
40         Hopedale
41        Hopkinton
42          Ipswich
43         Kingston
44        Lancaster
45         Lawrence
46        Leicester
47       Leominster
48        Lexington
49           Lowell
50             Lynn
51        Lynnfield
52           Malden
53        Mansfield
54         Medfield
55          Medford
56           Medway
57          Melrose
58           Mendon
59          Methuen
60          Milford
61         Millbury
62           Millis
63        Millville
64           Milton
65           Nahant
66        Nantucket
67           Natick
68          Needham
69    New Braintree
70           Newton
71     Northborough
72      Northbridge
73    North Andover
74    North Reading
75          Norwood
76          Peabody
77         Pembroke
78        Petersham
79         Plymouth
80     Provincetown
81           Quincy
82         Randolph
83          Raynham
84          Reading
85         Rehoboth
86           Revere
87            Salem
88           Saugus
89         Scituate
90          Seekonk
91           Sharon
92       Shrewsbury
93         Somerset
94       Somerville
95         Stoneham
96        Stoughton
97     Southborough
98      Southbridge
99          Spencer

In [23]:
# print the number of rows of the dataframe
kl_df.shape

(125, 1)

### 3. Get the geographical coordinates of all the neighborhoods 

In [24]:
# define a function to get coordinates
def get_latlng(neighborhood):
    # initialize your variable to None
    lat_lng_coords = None
    # loop until you get the coordinates
    while(lat_lng_coords is None):
        g = geocoder.arcgis('{},Boston,USA'.format(neighborhood))
        lat_lng_coords = g.latlng
    return lat_lng_coords

In [25]:
# call the function to get the coordinates, store in a new list using list comprehension
coords = [ get_latlng(neighborhood) for neighborhood in kl_df["Neighborhood"].tolist() ]

In [27]:
coords

[[42.61520321070313, -71.12685919732422],
 [42.35143165789913, -71.07047382894956],
 [41.95153800000001, -71.2603755],
 [42.94413924362768, -76.56060549496452],
 [42.310645233337695, -71.132661],
 [42.33672225081017, -71.14875823403028],
 [41.68481359326327, -70.26146151766287],
 [39.74256933847153, -84.85072791912101],
 [32.827125476025195, -97.14475265108241],
 [39.88822000000005, -81.19975999999997],
 [42.54040776982216, -71.24679534179991],
 [42.361528203481654, -71.05616188834757],
 [42.35866000000004, -71.05673999999993],
 [42.35224049999999, -71.065935],
 [42.356323668672594, -71.13545868672598],
 [42.00514052107693, -70.98225066054614],
 [42.27154299373975, -71.09841812929065],
 [42.28785350347664, -71.13257129909148],
 [42.34208586872748, -71.1039170368456],
 [36.07057916008346, -79.50799018649668],
 [42.361253413923, -71.06464494496335],
 [39.28392485275778, -76.58576357584049],
 [39.354304500000005, -74.45380275],
 [42.255689231381304, -71.14308226861867],
 [42.3484935905147

In [28]:
# create temporary dataframe to populate the coordinates into Latitude and Longitude
df_coords = pd.DataFrame(coords, columns=['Latitude', 'Longitude'])

In [29]:
# merge the coordinates into the original dataframe
kl_df['Latitude'] = df_coords['Latitude']
kl_df['Longitude'] = df_coords['Longitude']

In [31]:
# check the neighborhoods and the coordinates
print(kl_df.shape)
kl_df

(125, 3)


Neighborhood   Latitude  Longitude
0            Andover  42.615203 -71.126859
1          Arlington  42.351432 -71.070474
2          Attleboro  41.951538 -71.260375
3             Auburn  42.944139 -76.560605
4               Avon  42.310645 -71.132661
5               Ayer  42.336722 -71.148758
6         Barnstable  41.684814 -70.261462
7              Barre  39.742569 -84.850728
8            Bedford  32.827125 -97.144753
9            Belmont  39.888220 -81.199760
10         Billerica  42.540408 -71.246795
11        Blackstone  42.361528 -71.056162
12            Boston  42.358660 -71.056740
13          Boylston  42.352240 -71.065935
14         Braintree  42.356324 -71.135459
15       Bridgewater  42.005141 -70.982251
16          Brockton  42.271543 -71.098418
17        Brookfield  42.287854 -71.132571
18         Brookline  42.342086 -71.103917
19        Burlington  36.070579 -79.507990
20         Cambridge  42.361253 -71.064645
21            Canton  39.283925 -76.585764
22           Chelsea  39.354305 -74.453803
23            Dedham  42.255689 -71.143082
24           Dighton  42.348494 -71.155032
25           Duxbury  42.270791 -71.080558
26   East Brookfield  42.287854 -71.132571
27            Easton  42.359637 -71.131080
28         Edgartown  41.398589 -70.568559
29           Everett  42.400429 -71.045979
30         Fitchburg  43.043368 -89.455401
31        Foxborough  42.065870 -71.248390
32        Framingham  42.279730 -71.416390
33          Franklin  42.355713 -71.055522
34           Gardner  42.353221 -71.125858
35           Grafton  42.319881 -71.056305
36         Haverhill  42.773782 -71.095441
37           Hingham  42.189820 -70.897860
38          Holbrook  42.310310 -71.117276
39            Holden  42.366738 -71.052055
40          Hopedale  42.360176 -71.125832
41         Hopkinton  41.490410 -71.780600
42           Ipswich  42.347509 -71.093310
43          Kingston  42.352903 -71.059455
44         Lancaster  42.364066 -71.062403
45          Lawrence  42.721118 -71.150675
46         Leicester  42.351497 -71.153927
47        Leominster  42.526880 -71.761940
48         Lexington  37.976991 -84.553805
49            Lowell  42.619173 -71.310005
50              Lynn  42.463652 -70.976214
51         Lynnfield  42.516299 -71.026237
52            Malden  42.417599 -71.060100
53         Mansfield  40.765366 -82.554350
54          Medfield  42.345447 -71.105459
55           Medford  40.814469 -72.996503
56            Medway  42.271393 -71.064825
57           Melrose  42.349168 -71.067998
58            Mendon  42.350420 -71.048490
59           Methuen  42.722607 -71.153106
60           Milford  41.335183 -74.773501
61          Millbury  42.149932 -71.763462
62            Millis  42.321303 -71.083436
63         Millville  39.366990 -75.138264
64            Milton  42.353933 -71.056575
65            Nahant  42.287847 -71.052856
66         Nantucket  41.276535 -70.079936
67            Natick  42.358660 -71.056740
68           Needham  42.242495 -71.123261
69     New Braintree  42.356324 -71.135459
70            Newton  42.356827 -71.166736
71      Northborough  42.310630 -71.655050
72       Northbridge  42.154230 -71.651510
73     North Andover  42.636585 -71.089410
74     North Reading  42.330621 -71.073866
75           Norwood  42.291436 -71.045919
76           Peabody  42.569371 -71.029169
77          Pembroke  42.342652 -71.076969
78         Petersham  42.485620 -72.191840
79          Plymouth  41.247822 -75.926600
80      Provincetown  42.350040 -71.041710
81            Quincy  42.363288 -71.053693
82          Randolph  42.341407 -71.064934
83           Raynham  41.947120 -71.074030
84           Reading  42.330621 -71.073866
85          Rehoboth  41.838510 -71.274790
86            Revere  42.359503 -71.069242
87             Salem  30.857451 -83.783638
88            Saugus  42.463652 -70.976214
89          Scituate  42.199700 -70.752190
90           Seekonk  41.827900 -71.322650
91            Sharon  32.352682 -90.457089
92       

In [32]:
# save the DataFrame as CSV file
kl_df.to_csv("boston_neighbourhoods.csv", index=False)

### 4. Create a map of Boston including all neighborhoods

In [33]:
# get the coordinates of Kuala Lumpur
address = 'Boston,USA'

geolocator = Nominatim(user_agent="my-application")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Boston, United States is {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Boston, United States is 42.3602534, -71.0582912.


In [34]:
# create map of Boston using latitude and longitude values
map_kl = folium.Map(location=[latitude, longitude], zoom_start=11)

# add markers to map
for lat, lng, neighborhood in zip(kl_df['Latitude'], kl_df['Longitude'], kl_df['Neighborhood']):
    label = '{}'.format(neighborhood)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7).add_to(map_kl)  
    
map_kl

In [35]:
# save the map as HTML file
map_kl.save('Boston_neighborhood_map.html')

### 5. Use the Foursquare API to explore the neighborhoods

In [180]:
# define Foursquare Credentials and Version
CLIENT_ID = 'Your client ID' # your Foursquare ID
CLIENT_SECRET = 'Your secret ID' # your Foursquare Secret
VERSION = '20190822' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: Your client ID
CLIENT_SECRET:Your secret ID


**Now, let's get the top 100 venues that are within a radius of 5000 meters.**

In [153]:
radius = 5000
LIMIT = 100

venues = []

for lat, long, neighborhood in zip(kl_df['Latitude'], kl_df['Longitude'], kl_df['Neighborhood']):
    
    # create the API request URL
    url = "https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}".format(
        CLIENT_ID,
        CLIENT_SECRET,
        VERSION,
        lat,
        long,
        radius, 
        LIMIT)
    
    # make the GET request
    results = requests.get(url).json()["response"]['groups'][0]['items']
    
    # return only relevant information for each nearby venue
    for venue in results:
        venues.append((
            neighborhood,
            lat, 
            long, 
            venue['venue']['name'], 
            venue['venue']['location']['lat'], 
            venue['venue']['location']['lng'],  
            venue['venue']['categories'][0]['name']))

In [154]:
# convert the venues list into a new DataFrame
venues_df = pd.DataFrame(venues)

# define the column names
venues_df.columns = ['Neighborhood', 'Latitude', 'Longitude', 'Venue_Name', 'Venue_Latitude', 'Venue_Longitude', 'Venue_Category']

print(venues_df.shape)
venues_df.head()

(10986, 7)


Neighborhood   Latitude  Longitude                  Venue_Name  \
0      Andover  42.615203 -71.126859            Tokyo Steakhouse   
1      Andover  42.615203 -71.126859         Town Market Andover   
2      Andover  42.615203 -71.126859  Harold Parker State Forest   
3      Andover  42.615203 -71.126859                   Starbucks   
4      Andover  42.615203 -71.126859       Phillips Academy Rink   

   Venue_Latitude  Venue_Longitude     Venue_Category  
0       42.602374       -71.121367   Sushi Restaurant  
1       42.618599       -71.125611  Food & Drink Shop  
2       42.608443       -71.091499             Forest  
3       42.591507       -71.117075        Coffee Shop  
4       42.641782       -71.129722       Skating Rink

**Let's check how many venues were returned for each neighorhood**

In [156]:
venues_df.groupby(["Neighborhood"]).count()

Latitude  Longitude  Venue_Name  Venue_Latitude  \
Neighborhood                                                       
Andover                95         95          95              95   
Arlington             100        100         100             100   
Attleboro              56         56          56              56   
Auburn                 99         99          99              99   
Avon                  100        100         100             100   
Ayer                  100        100         100             100   
Barnstable            100        100         100             100   
Barre                   1          1           1               1   
Bedford               100        100         100             100   
Belmont                 2          2           2               2   
Billerica              67         67          67              67   
Blackstone            100        100         100             100   
Boston                100        100         100             100   
Boylston              100        100         100             100   
Braintree             100        100         100             100   
Bridgewater            98         98          98              98   
Brockton              100        100         100             100   
Brookfield            100        100         100             100   
Brookline             100        100         100             100   
Burlington            100        100         100             100   
Cambridge             100        100         100             100   
Canton                100        100         100             100   
Chelsea               100        100         100             100   
Dedham                100        100         100             100   
Dighton               100        100         100             100   
Duxbury               100        100         100             100   
East Brookfield       100        100         100             100   
Easton                100        100         100             100   
Edgartown              71         71          71              71   
Everett               100        100         100             100   
Fitchburg             100        100         100             100   
Foxborough            100        100         100             100   
Framingham            100        100         100             100   
Franklin              100        100         100             100   
Gardner               100        100         100             100   
Grafton               100        100         100             100   
Haverhill             100        100         100             100   
Hingham               100        100         100             100   
Holbrook              100        100         100             100   
Holden                100        100         100             100   
Hopedale              100        100         100             100   
Hopkinton              10         10          10              10   
Ipswich               100        100         100             100   
Kingston              100        100         100             100   
Lancaster             100        100         100             100   
Lawrence              100        100         100             100   
Leicester             100        100         100             100   
Leominster            100        100         100             100   
Lexington             100        100         100             100   
Lowell                100        100         100             100   
Lynn                  100        100         100             100   
Lynnfield             100        100         100             100   
Malden                100        100         100             100   
Mansfield              96         96          96              96   
Medfield              100        100         100             100   
Medford               100        100         100             100   
Medway                100        100         100             100   
Melro

**Let's find out how many unique categories from all the returned venues**

In [157]:
print('There are {} uniques categories.'.format(len(venues_df['Venue_Category'].unique())))

There are 340 uniques categories.


In [158]:
# print out the list of categories
venues_df['Venue_Category'].unique()[:50]

array(['Sushi Restaurant', 'Food & Drink Shop', 'Forest', 'Coffee Shop',
       'Skating Rink', 'Pizza Place', 'Trail', 'Italian Restaurant',
       'Mediterranean Restaurant', 'Golf Course', 'American Restaurant',
       'Donut Shop', 'Brewery', 'Bagel Shop', 'Art Museum',
       'Big Box Store', 'Bookstore', 'Chinese Restaurant',
       'Seafood Restaurant', 'Burger Joint', 'Gym', 'Farm',
       'Fast Food Restaurant', 'Pharmacy', 'Park', 'Weight Loss Center',
       'Liquor Store', 'Sporting Goods Shop', 'Sandwich Place', 'Hotel',
       'Gift Shop', 'Shipping Store', 'Mexican Restaurant',
       'Mobile Phone Shop', 'Café', 'Sports Bar', 'Automotive Shop',
       'Pub', 'Grocery Store', 'Tex-Mex Restaurant', 'Lake', 'Shoe Store',
       'Campground', 'Health & Beauty Service', 'Shop & Service',
       'Gourmet Shop', 'Boat or Ferry', 'Paintball Field',
       'Storage Facility', 'Pet Store'], dtype=object)

In [159]:
"Neighborhood" in venues_df['Venue_Category'].unique()

True

### 6. Analyze Each Neighborhood

In [161]:
# one hot encoding
kl_onehot = pd.get_dummies(venues_df[['Venue_Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
kl_onehot['Neighborhoods'] = venues_df['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [kl_onehot.columns[-1]] + list(kl_onehot.columns[:-1])
kl_onehot = kl_onehot[fixed_columns]

print(kl_onehot.shape)
kl_onehot.head(100)

(10986, 341)


Neighborhoods  ATM  Accessories Store  African Restaurant  Airport  \
0        Andover    0                  0                   0        0   
1        Andover    0                  0                   0        0   
2        Andover    0                  0                   0        0   
3        Andover    0                  0                   0        0   
4        Andover    0                  0                   0        0   
5        Andover    0                  0                   0        0   
6        Andover    0                  0                   0        0   
7        Andover    0                  0                   0        0   
8        Andover    0                  0                   0        0   
9        Andover    0                  0                   0        0   
10       Andover    0                  0                   0        0   
11       Andover    0                  0                   0        0   
12       Andover    0                  0                   0        0   
13       Andover    0                  0                   0        0   
14       Andover    0                  0                   0        0   
15       Andover    0                  0                   0        0   
16       Andover    0                  0                   0        0   
17       Andover    0                  0                   0        0   
18       Andover    0                  0                   0        0   
19       Andover    0                  0                   0        0   
20       Andover    0                  0                   0        0   
21       Andover    0                  0                   0        0   
22       Andover    0                  0                   0        0   
23       Andover    0                  0                   0        0   
24       Andover    0                  0                   0        0   
25       Andover    0                  0                   0        0   
26       Andover    0                  0                   0        0   
27       Andover    0                  0                   0        0   
28       Andover    0                  0                   0        0   
29       Andover    0                  0                   0        0   
30       Andover    0                  0                   0        0   
31       Andover    0                  0                   0        0   
32       Andover    0                  0                   0        0   
33       Andover    0                  0                   0        0   
34       Andover    0                  0                   0        0   
35       Andover    0                  0                   0        0   
36       Andover    0                  0                   0        0   
37       Andover    0                  0                   0        0   
38       Andover    0                  0                   0        0   
39       Andover    0                  0                   0        0   
40       Andover    0                  0                   0        0   
41       Andover    0                  0                   0        0   
42       Andover    0                  0                   0        0   
43       Andover    0                  0                   0        0   
44       Andover    0                  0                   0        0   
45       Andover    0                  0                   0        0   
46       Andover    0                  0                   0        0   
47       Andover    0                  0                   0        0   
48       Andover    0                  0                   0        0   
49       Andover    0                  0                   0        0   
50       Andover    0                  0                   0        0   
51       Andover    0                  0                   0        0   
52       Andover    0                  0                   0        0   
53       Andover    0                  0                   0 

**Next, let's group rows by neighborhood and by taking the mean of the frequency of occurrence of each category**

In [162]:
kl_grouped = kl_onehot.groupby(["Neighborhoods"]).mean().reset_index()

print(kl_grouped.shape)
kl_grouped

(125, 341)


Neighborhoods       ATM  Accessories Store  African Restaurant  \
0            Andover  0.000000           0.000000                0.00   
1          Arlington  0.000000           0.000000                0.00   
2          Attleboro  0.000000           0.000000                0.00   
3             Auburn  0.000000           0.000000                0.00   
4               Avon  0.000000           0.000000                0.00   
5               Ayer  0.000000           0.000000                0.00   
6         Barnstable  0.000000           0.000000                0.00   
7              Barre  0.000000           0.000000                0.00   
8            Bedford  0.000000           0.000000                0.00   
9            Belmont  0.000000           0.000000                0.00   
10         Billerica  0.014925           0.000000                0.00   
11        Blackstone  0.000000           0.000000                0.00   
12            Boston  0.000000           0.000000                0.00   
13          Boylston  0.000000           0.000000                0.00   
14         Braintree  0.000000           0.000000                0.00   
15       Bridgewater  0.000000           0.000000                0.00   
16          Brockton  0.000000           0.010000                0.00   
17        Brookfield  0.000000           0.010000                0.00   
18         Brookline  0.000000           0.000000                0.00   
19        Burlington  0.000000           0.000000                0.00   
20         Cambridge  0.000000           0.000000                0.00   
21            Canton  0.000000           0.000000                0.00   
22           Chelsea  0.000000           0.000000                0.00   
23            Dedham  0.000000           0.000000                0.00   
24           Dighton  0.000000           0.000000                0.00   
25           Duxbury  0.000000           0.000000                0.00   
26   East Brookfield  0.000000           0.010000                0.00   
27            Easton  0.000000           0.000000                0.00   
28         Edgartown  0.000000           0.000000                0.00   
29           Everett  0.000000           0.000000                0.00   
30         Fitchburg  0.000000           0.000000                0.00   
31        Foxborough  0.000000           0.010000                0.00   
32        Framingham  0.000000           0.000000                0.00   
33          Franklin  0.000000           0.000000                0.00   
34           Gardner  0.000000           0.000000                0.00   
35           Grafton  0.000000           0.000000                0.00   
36         Haverhill  0.000000           0.000000                0.00   
37           Hingham  0.000000           0.000000                0.00   
38          Holbrook  0.000000           0.010000                0.00   
39            Holden  0.000000           0.000000                0.00   
40          Hopedale  0.000000           0.000000                0.00   
41         Hopkinton  0.000000           0.000000                0.00   
42           Ipswich  0.000000           0.000000                0.00   
43          Kingston  0.000000           0.000000                0.00   
44         Lancaster  0.000000           0.000000                0.00   
45          Lawrence  0.000000           0.000000                0.00   
46         Leicester  0.000000           0.000000                0.00   
47        Leominster  0.000000           0.000000                0.00   
48         Lexington  0.000000           0.000000                0.00   
49            Lowell  0.000000           0.000000                0.00   
50              Lynn  0.000000           0.000000                0.00   
51         Lynnfield  0.000000           0.010000                0.00   
52            Malden  0.000000           0.000000                0.00   
53         Mansfield  0.000000           0.000000                

In [163]:
len(kl_grouped[kl_grouped["Pizza Place"] > 0])

115

**Create a new DataFrame for pizza places**

In [164]:
kl_pizza = kl_grouped[["Neighborhoods","Pizza Place"]]

In [165]:
kl_pizza.head(100)

Neighborhoods  Pizza Place
0           Andover     0.042105
1         Arlington     0.010000
2         Attleboro     0.071429
3            Auburn     0.050505
4              Avon     0.060000
5              Ayer     0.100000
6        Barnstable     0.050000
7             Barre     0.000000
8           Bedford     0.010000
9           Belmont     0.000000
10        Billerica     0.074627
11       Blackstone     0.030000
12           Boston     0.030000
13         Boylston     0.020000
14        Braintree     0.060000
15      Bridgewater     0.061224
16         Brockton     0.020000
17       Brookfield     0.030000
18        Brookline     0.040000
19       Burlington     0.040000
20        Cambridge     0.030000
21           Canton     0.040000
22          Chelsea     0.020000
23           Dedham     0.020000
24          Dighton     0.100000
25          Duxbury     0.050000
26  East Brookfield     0.030000
27           Easton     0.070000
28        Edgartown     0.028169
29          Everett     0.080000
30        Fitchburg     0.030000
31       Foxborough     0.010000
32       Framingham     0.030000
33         Franklin     0.050000
34          Gardner     0.080000
35          Grafton     0.020000
36        Haverhill     0.050000
37          Hingham     0.060000
38         Holbrook     0.060000
39           Holden     0.040000
40         Hopedale     0.070000
41        Hopkinton     0.000000
42          Ipswich     0.030000
43         Kingston     0.050000
44        Lancaster     0.030000
45         Lawrence     0.080000
46        Leicester     0.090000
47       Leominster     0.040000
48        Lexington     0.020000
49           Lowell     0.090000
50             Lynn     0.070000
51        Lynnfield     0.050000
52           Malden     0.050000
53        Mansfield     0.020833
54         Medfield     0.030000
55          Medford     0.110000
56           Medway     0.060000
57          Melrose     0.020000
58           Mendon     0.050000
59          Methuen     0.080000
60          Milford     0.078431
61         Millbury     0.078947
62           Millis     0.030000
63        Millville     0.000000
64           Milton     0.050000
65           Nahant     0.040000
66        Nantucket     0.020000
67           Natick     0.030000
68          Needham     0.020000
69    New Braintree     0.060000
70           Newton     0.060000
71    North Andover     0.015873
72    North Reading     0.030000
73     Northborough     0.040000
74      Northbridge     0.068182
75          Norwood     0.030000
76          Peabody     0.037037
77         Pembroke     0.030000
78        Petersham     0.000000
79         Plymouth     0.130000
80     Provincetown     0.040000
81           Quincy     0.040000
82         Randolph     0.020000
83          Raynham     0.059524
84          Reading     0.030000
85         Rehoboth     0.030303
86           Revere     0.020000
87            Salem     0.000000
88           Saugus     0.070000
89         Scituate     0.073171
90          Seekonk     0.015385
91           Sharon     0.000000
92       Shrewsbury     0.030000
93         Somerset     0.040000
94       Somerville     0.050000
95     Southborough     0.062500
96      Southbridge     0.097561
97          Spencer     0.020000
98         Stoneham     0.070000
99        Stoughton     0.020000

### 7. Cluster Neighborhoods
Run k-means to cluster the neighborhoods in Kuala Lumpur into 3 clusters.

In [166]:
# set number of clusters
kclusters = 3

kl_clustering = kl_pizza.drop(["Neighborhoods"], 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(kl_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([2, 0, 1, 2, 2, 1, 2, 0, 0, 0])

In [169]:
# Create a new dataframe that includes the cluster label
kl_merged = kl_pizza.copy()

# add clustering labels
kl_merged["Cluster Labels"] = kmeans.labels_

In [170]:
kl_merged.rename(columns={"Neighborhoods": "Neighborhood"}, inplace=True)
kl_merged.head(100)

Neighborhood  Pizza Place  Cluster Labels
0           Andover     0.042105               2
1         Arlington     0.010000               0
2         Attleboro     0.071429               1
3            Auburn     0.050505               2
4              Avon     0.060000               2
5              Ayer     0.100000               1
6        Barnstable     0.050000               2
7             Barre     0.000000               0
8           Bedford     0.010000               0
9           Belmont     0.000000               0
10        Billerica     0.074627               1
11       Blackstone     0.030000               0
12           Boston     0.030000               0
13         Boylston     0.020000               0
14        Braintree     0.060000               2
15      Bridgewater     0.061224               2
16         Brockton     0.020000               0
17       Brookfield     0.030000               0
18        Brookline     0.040000               2
19       Burlington     0.040000               2
20        Cambridge     0.030000               0
21           Canton     0.040000               2
22          Chelsea     0.020000               0
23           Dedham     0.020000               0
24          Dighton     0.100000               1
25          Duxbury     0.050000               2
26  East Brookfield     0.030000               0
27           Easton     0.070000               1
28        Edgartown     0.028169               0
29          Everett     0.080000               1
30        Fitchburg     0.030000               0
31       Foxborough     0.010000               0
32       Framingham     0.030000               0
33         Franklin     0.050000               2
34          Gardner     0.080000               1
35          Grafton     0.020000               0
36        Haverhill     0.050000               2
37          Hingham     0.060000               2
38         Holbrook     0.060000               2
39           Holden     0.040000               2
40         Hopedale     0.070000               1
41        Hopkinton     0.000000               0
42          Ipswich     0.030000               0
43         Kingston     0.050000               2
44        Lancaster     0.030000               0
45         Lawrence     0.080000               1
46        Leicester     0.090000               1
47       Leominster     0.040000               2
48        Lexington     0.020000               0
49           Lowell     0.090000               1
50             Lynn     0.070000               1
51        Lynnfield     0.050000               2
52           Malden     0.050000               2
53        Mansfield     0.020833               0
54         Medfield     0.030000               0
55          Medford     0.110000               1
56           Medway     0.060000               2
57          Melrose     0.020000               0
58           Mendon     0.050000               2
59          Methuen     0.080000               1
60          Milford     0.078431               1
61         Millbury     0.078947               1
62           Millis     0.030000               0
63        Millville     0.000000               0
64           Milton     0.050000               2
65           Nahant     0.040000               2
66        Nantucket     0.020000               0
67           Natick     0.030000               0
68          Needham     0.020000               0
69    New Braintree     0.060000               2
70           Newton     0.060000               2
71    North Andover     0.015873               0
72    North Reading     0.030000               0
73     Northborough     0.040000               2
74      Northbridge     0.068182               1
75          Norwood     0.030000               0
76          Peabody     0.037037               2
77         Pembroke     0.030000               0
78        Petersham     0.000000               0
79         Plymouth     0.130000               1
80     Provincetown     0.040000      

In [171]:
# Merge with the neighborhood datframe to get latitude/longitude for each neighborhood
kl_merged = kl_merged.join(kl_df.set_index("Neighborhood"), on="Neighborhood")

print(kl_merged.shape)
kl_merged.head() # check the last columns!

(125, 5)


Neighborhood  Pizza Place  Cluster Labels   Latitude  Longitude
0      Andover     0.042105               2  42.615203 -71.126859
1    Arlington     0.010000               0  42.351432 -71.070474
2    Attleboro     0.071429               1  41.951538 -71.260375
3       Auburn     0.050505               2  42.944139 -76.560605
4         Avon     0.060000               2  42.310645 -71.132661

In [172]:
# Sort the results by Cluster Labels
print(kl_merged.shape)
kl_merged.sort_values(["Cluster Labels"], inplace=True)
kl_merged

(125, 5)


Neighborhood  Pizza Place  Cluster Labels   Latitude  Longitude
62            Millis     0.030000               0  42.321303 -71.083436
86            Revere     0.020000               0  42.359503 -71.069242
85          Rehoboth     0.030303               0  41.838510 -71.274790
84           Reading     0.030000               0  42.330621 -71.073866
82          Randolph     0.020000               0  42.341407 -71.064934
78         Petersham     0.000000               0  42.485620 -72.191840
77          Pembroke     0.030000               0  42.342652 -71.076969
75           Norwood     0.030000               0  42.291436 -71.045919
72     North Reading     0.030000               0  42.330621 -71.073866
71     North Andover     0.015873               0  42.636585 -71.089410
68           Needham     0.020000               0  42.242495 -71.123261
67            Natick     0.030000               0  42.358660 -71.056740
66         Nantucket     0.020000               0  41.276535 -70.079936
63         Millville     0.000000               0  39.366990 -75.138264
123           Woburn     0.020000               0  42.360219 -71.067425
57           Melrose     0.020000               0  42.349168 -71.067998
54          Medfield     0.030000               0  42.345447 -71.105459
53         Mansfield     0.020833               0  40.765366 -82.554350
87             Salem     0.000000               0  30.857451 -83.783638
90           Seekonk     0.015385               0  41.827900 -71.322650
91            Sharon     0.000000               0  32.352682 -90.457089
92        Shrewsbury     0.030000               0  42.274420 -71.754592
121       Winchester     0.020000               0  42.349620 -71.068395
119         Weymouth     0.020000               0  42.266735 -71.152546
118           Weston     0.010000               0  42.348970 -71.077340
117      Westborough     0.030000               0  42.284170 -71.599240
116     West Tisbury     0.000000               0  41.381390 -70.674530
115  West Brookfield     0.030000               0  42.287854 -71.132571
114        Wellesley     0.000000               0  42.295350 -71.065829
112          Wayland     0.030000               0  42.313671 -71.075290
48         Lexington     0.020000               0  37.976991 -84.553805
111        Watertown     0.000000               0  37.779906 -85.677265
109          Walpole     0.031915               0  42.148710 -71.250950
108        Wakefield     0.030000               0  42.243036 -71.125300
106            Upton     0.020000               0  42.342413 -71.072280
104         Townsend     0.020000               0  42.319355 -71.092204
102          Taunton     0.030000               0  42.267576 -71.107005
101          Swansea     0.020000               0  30.678211 -88.138220
99         Stoughton     0.020000               0  42.336019 -71.071482
97           Spencer     0.020000               0  42.294080 -71.076198
110          Waltham     0.020000               0  42.342204 -71.069452
44         Lancaster     0.030000               0  42.364066 -71.062403
124        Worcester     0.030000               0  42.255923 -71.761501
11        Blackstone     0.030000               0  42.361528 -71.056162
32        Framingham     0.030000               0  42.279730 -71.416390
9            Belmont     0.000000               0  39.888220 -81.199760
12            Boston     0.030000               0  42.358660 -71.056740
8            Bedford     0.010000               0  32.827125 -97.144753
35           Grafton     0.020000               0  42.319881 -71.056305
7              Barre     0.000000               0  39.742569 -84.850728
28         Edgartown     0.028169               0  41.398589 -70.568559
30         Fitchburg     0.030000               0  43.043368 -89.455401
26   East Brookfield     0.030000               0  42.287854 -71.132571
42           Ipswich     0.030000               0  42.347509 -71.093310
13          Boylston     0.020000               

**Finally, let's visualize the resulting clusters**

In [173]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i+x+(i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(kl_merged['Latitude'], kl_merged['Longitude'], kl_merged['Neighborhood'], kl_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' - Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [174]:
# save the map as HTML file
map_clusters.save('Boston_neighborhood_map_clusters.html')

### 8. Examine Clusters

#### Cluster 0

In [175]:
kl_merged.loc[kl_merged['Cluster Labels'] == 0]

Neighborhood  Pizza Place  Cluster Labels   Latitude  Longitude
62            Millis     0.030000               0  42.321303 -71.083436
86            Revere     0.020000               0  42.359503 -71.069242
85          Rehoboth     0.030303               0  41.838510 -71.274790
84           Reading     0.030000               0  42.330621 -71.073866
82          Randolph     0.020000               0  42.341407 -71.064934
78         Petersham     0.000000               0  42.485620 -72.191840
77          Pembroke     0.030000               0  42.342652 -71.076969
75           Norwood     0.030000               0  42.291436 -71.045919
72     North Reading     0.030000               0  42.330621 -71.073866
71     North Andover     0.015873               0  42.636585 -71.089410
68           Needham     0.020000               0  42.242495 -71.123261
67            Natick     0.030000               0  42.358660 -71.056740
66         Nantucket     0.020000               0  41.276535 -70.079936
63         Millville     0.000000               0  39.366990 -75.138264
123           Woburn     0.020000               0  42.360219 -71.067425
57           Melrose     0.020000               0  42.349168 -71.067998
54          Medfield     0.030000               0  42.345447 -71.105459
53         Mansfield     0.020833               0  40.765366 -82.554350
87             Salem     0.000000               0  30.857451 -83.783638
90           Seekonk     0.015385               0  41.827900 -71.322650
91            Sharon     0.000000               0  32.352682 -90.457089
92        Shrewsbury     0.030000               0  42.274420 -71.754592
121       Winchester     0.020000               0  42.349620 -71.068395
119         Weymouth     0.020000               0  42.266735 -71.152546
118           Weston     0.010000               0  42.348970 -71.077340
117      Westborough     0.030000               0  42.284170 -71.599240
116     West Tisbury     0.000000               0  41.381390 -70.674530
115  West Brookfield     0.030000               0  42.287854 -71.132571
114        Wellesley     0.000000               0  42.295350 -71.065829
112          Wayland     0.030000               0  42.313671 -71.075290
48         Lexington     0.020000               0  37.976991 -84.553805
111        Watertown     0.000000               0  37.779906 -85.677265
109          Walpole     0.031915               0  42.148710 -71.250950
108        Wakefield     0.030000               0  42.243036 -71.125300
106            Upton     0.020000               0  42.342413 -71.072280
104         Townsend     0.020000               0  42.319355 -71.092204
102          Taunton     0.030000               0  42.267576 -71.107005
101          Swansea     0.020000               0  30.678211 -88.138220
99         Stoughton     0.020000               0  42.336019 -71.071482
97           Spencer     0.020000               0  42.294080 -71.076198
110          Waltham     0.020000               0  42.342204 -71.069452
44         Lancaster     0.030000               0  42.364066 -71.062403
124        Worcester     0.030000               0  42.255923 -71.761501
11        Blackstone     0.030000               0  42.361528 -71.056162
32        Framingham     0.030000               0  42.279730 -71.416390
9            Belmont     0.000000               0  39.888220 -81.199760
12            Boston     0.030000               0  42.358660 -71.056740
8            Bedford     0.010000               0  32.827125 -97.144753
35           Grafton     0.020000               0  42.319881 -71.056305
7              Barre     0.000000               0  39.742569 -84.850728
28         Edgartown     0.028169               0  41.398589 -70.568559
30         Fitchburg     0.030000               0  43.043368 -89.455401
26   East Brookfield     0.030000               0  42.287854 -71.132571
42           Ipswich     0.030000               0  42.347509 -71.093310
13          Boylston     0.020000               

#### Cluster 1

In [176]:
kl_merged.loc[kl_merged['Cluster Labels'] == 1]

Neighborhood  Pizza Place  Cluster Labels   Latitude  Longitude
79      Plymouth     0.130000               1  41.247822 -75.926600
27        Easton     0.070000               1  42.359637 -71.131080
107     Uxbridge     0.078125               1  42.082582 -71.636737
29       Everett     0.080000               1  42.400429 -71.045979
88        Saugus     0.070000               1  42.463652 -70.976214
89      Scituate     0.073171               1  42.199700 -70.752190
74   Northbridge     0.068182               1  42.154230 -71.651510
24       Dighton     0.100000               1  42.348494 -71.155032
98      Stoneham     0.070000               1  42.550430 -71.262970
10     Billerica     0.074627               1  42.540408 -71.246795
50          Lynn     0.070000               1  42.463652 -70.976214
2      Attleboro     0.071429               1  41.951538 -71.260375
96   Southbridge     0.097561               1  42.074520 -72.032680
55       Medford     0.110000               1  40.814469 -72.996503
49        Lowell     0.090000               1  42.619173 -71.310005
5           Ayer     0.100000               1  42.336722 -71.148758
46     Leicester     0.090000               1  42.351497 -71.153927
59       Methuen     0.080000               1  42.722607 -71.153106
60       Milford     0.078431               1  41.335183 -74.773501
61      Millbury     0.078947               1  42.149932 -71.763462
45      Lawrence     0.080000               1  42.721118 -71.150675
34       Gardner     0.080000               1  42.353221 -71.125858
40      Hopedale     0.070000               1  42.360176 -71.125832

#### Cluster 2

In [177]:
kl_merged.loc[kl_merged['Cluster Labels'] == 2]

Neighborhood  Pizza Place  Cluster Labels   Latitude  Longitude
15     Bridgewater     0.061224               2  42.005141 -70.982251
122       Winthrop     0.050000               2  42.354970 -71.057687
103      Tewksbury     0.053191               2  42.611590 -71.232650
100     Swampscott     0.050000               2  42.469730 -70.920030
14       Braintree     0.060000               2  42.356324 -71.135459
3           Auburn     0.050505               2  42.944139 -76.560605
105   Tyngsborough     0.050633               2  42.676650 -71.425600
4             Avon     0.060000               2  42.310645 -71.132661
6       Barnstable     0.050000               2  41.684814 -70.261462
113        Webster     0.040000               2  42.364764 -71.052914
120     Wilmington     0.050000               2  42.279590 -71.075654
43        Kingston     0.050000               2  42.352903 -71.059455
83         Raynham     0.059524               2  41.947120 -71.074030
95    Southborough     0.062500               2  42.301289 -71.503456
47      Leominster     0.040000               2  42.526880 -71.761940
51       Lynnfield     0.050000               2  42.516299 -71.026237
52          Malden     0.050000               2  42.417599 -71.060100
39          Holden     0.040000               2  42.366738 -71.052055
38        Holbrook     0.060000               2  42.310310 -71.117276
56          Medway     0.060000               2  42.271393 -71.064825
37         Hingham     0.060000               2  42.189820 -70.897860
58          Mendon     0.050000               2  42.350420 -71.048490
36       Haverhill     0.050000               2  42.773782 -71.095441
64          Milton     0.050000               2  42.353933 -71.056575
65          Nahant     0.040000               2  42.287847 -71.052856
33        Franklin     0.050000               2  42.355713 -71.055522
69   New Braintree     0.060000               2  42.356324 -71.135459
70          Newton     0.060000               2  42.356827 -71.166736
73    Northborough     0.040000               2  42.310630 -71.655050
76         Peabody     0.037037               2  42.569371 -71.029169
80    Provincetown     0.040000               2  42.350040 -71.041710
81          Quincy     0.040000               2  42.363288 -71.053693
25         Duxbury     0.050000               2  42.270791 -71.080558
21          Canton     0.040000               2  39.283925 -76.585764
19      Burlington     0.040000               2  36.070579 -79.507990
93        Somerset     0.040000               2  40.524682 -74.579942
94      Somerville     0.050000               2  42.385780 -71.085630
18       Brookline     0.040000               2  42.342086 -71.103917
0          Andover     0.042105               2  42.615203 -71.126859

In [179]:
cluster_0 = kl_merged.loc[kl_merged['Cluster Labels'] == 0]
len_cluster_0 = len(cluster_0)

cluster_1 = kl_merged.loc[kl_merged['Cluster Labels'] == 1]
len_cluster_1 = len(cluster_1)

cluster_2 = kl_merged.loc[kl_merged['Cluster Labels'] == 2]
len_cluster_2 = len(cluster_2)

print('Total neighborhoods in cluster 0 =', len_cluster_0)
print('Total neighborhoods in cluster 1 =', len_cluster_1)
print('Total neighborhoods in cluster 2 =', len_cluster_2)

Total neighborhoods in cluster 0 = 63
Total neighborhoods in cluster 1 = 23
Total neighborhoods in cluster 2 = 39


#### Observations:

The results from the k-means clustering showing that we can categorize the neighbourhoods into 3 clusters based on the frequency of occurrence for “Pizza Places”: 

    • Cluster 0: Neighbourhoods with high concentration of pizza places; around 51%
    • Cluster 1: Neighbourhoods with low concentration of pizza places; around 18%
    • Cluster 2: Neighbourhoods with medium concentration of pizza places; around 31%

The results of the clustering are visualized in the map below with cluster 0 in RED color, cluster 1 in PURPLE color, and cluster 2 in MINT GREEN color 

Analysis showing that most of the pizza places are concentrated in cluster 0 which include Boston downtown, Fenway, Backbay, South end and some of the financial district area (around 51%). Cluster 1 have around 18% concentration and cluster 2 have around 31%.  This is showing that new pizza places can be opened in neighborhoods listed in cluster 1 as less competition compared to cluster 0 and 2. Meanwhile, pizza places in cluster 0 are likely suffering from intense competition due to oversupply and high concentration. Pizza places with unique menus and special varieties can survive from the competition and can open on these neighborhoods . Therefore, this project recommends that new investors looking to start pizza places in Boston neighborhoods to capitalize on these findings to open new pizza places in neighborhoods of cluster 1 unless there is a unique specialty on their menu